In [14]:
import os
import sys
import urllib, io
os.getcwd()
sys.path.append("..")
sys.path.append("../utils")
proj_dir = os.path.abspath('../..')

## add helpers to python path
if os.path.join(proj_dir,'stimuli') not in sys.path:
    sys.path.append(os.path.join(proj_dir,'stimuli'))

import numpy as np
import scipy.stats as stats
import pandas as pd
from scipy import stats
from scipy.spatial import distance
from scipy import ndimage
from scipy.stats import entropy
from random import random
from sklearn.cluster import SpectralBiclustering
import itertools

import pymongo as pm
from collections import Counter
import json
import re
import ast

from PIL import Image, ImageOps, ImageDraw, ImageFont 

from io import BytesIO
import base64

import  matplotlib
from matplotlib import pylab, mlab, pyplot
%matplotlib inline
from IPython.core.pylabtools import figsize, getfigs
plt = pyplot
import matplotlib as mpl
mpl.rcParams['pdf.fonttype'] = 42
from matplotlib import colors

import seaborn as sns
sns.set_context('talk')
sns.set_style('darkgrid')

from IPython.display import clear_output

import warnings
warnings.filterwarnings("ignore", category=DeprecationWarning)
warnings.filterwarnings("ignore", message="numpy.dtype size changed")
warnings.filterwarnings("ignore", message="numpy.ufunc size changed")

import plotly
import plotly.graph_objects as go
import plotly.io as pio
pio.orca.config.use_xvfb = True
plotly.io.orca.config.save()

import importlib
import trajectory as g

In [15]:
## directory & file hierarchy
proj_dir = os.path.abspath('../..')
datavol_dir = os.path.join(proj_dir,'data')
analysis_dir = os.path.abspath(os.path.join(os.getcwd(),'..'))
results_dir = os.path.join(analysis_dir,'results')
stim_dir = os.path.join(proj_dir,'stimuli')
plot_dir = os.path.join(results_dir,'plots')
csv_dir = os.path.join(results_dir,'csv')
json_dir = os.path.join(results_dir,'json')
exp_dir = os.path.abspath(os.path.join(proj_dir,'experiments'))
png_dir = os.path.abspath(os.path.join(datavol_dir,'png'))
jefan_dir = os.path.join(analysis_dir,'jefan')
will_dir = os.path.join(analysis_dir,'will')
    
if not os.path.exists(results_dir):
    os.makedirs(results_dir)
    
if not os.path.exists(plot_dir):
    os.makedirs(plot_dir)   
    
if not os.path.exists(csv_dir):
    os.makedirs(csv_dir)       

### load in data

In [16]:
iteration_name = 'Exp2Pilot3_all'
num_trials = 24 #for sanity checks

In [17]:
# Data already compiled into dataframes in CogSci 2020 Dataframe Generator

# trial_end data
trial_path = os.path.join(csv_dir,'block_silhouette_{}_good.csv'.format(iteration_name))
df = pd.read_csv(trial_path)

# # initial_block data
initial_path = os.path.join(csv_dir,'block_silhouette_initial_{}_good.csv'.format(iteration_name))
dfi = pd.read_csv(initial_path)

# # settled_block data
settled_path = os.path.join(csv_dir,'block_silhouette_settled_{}_good.csv'.format(iteration_name))
dfs = pd.read_csv(settled_path)

# # Sanity Check- same participants in each dataset.
df_participants = df.gameID.unique()
dfs_participants = dfs.gameID.unique()
assert Counter(df_participants) == Counter(dfs_participants)

n_before_outliers = len(df_participants)
print(str(n_before_outliers) + ' participants total')

105 participants total


### apply preprocessing

In [18]:
targets = np.sort(df['targetName'].unique())
ppts = np.sort(df['gameID'].unique())
reps = np.sort(df['repetition'].unique())

dfi['usableDiscreteWorld'] = dfi['discreteWorld'].apply(lambda a: 1+(-1)*np.array(ast.literal_eval(a)))
dfi['flatDiscreteWorld'] = dfi['discreteWorld'].apply(lambda a: (1+(-1)*np.array(ast.literal_eval(a))).flatten())

dfic = dfi.copy()
#dfic = dfi[dfi.condition=='repeated']
dfic = dfic[['targetName','gameID','blockNum','repetition','phase_extended','flatDiscreteWorld','usableDiscreteWorld','rawF1DiscreteScore']]
dfic['discreteWorld'] = dfic['usableDiscreteWorld']
dfic['flatDiscreteWorldStr'] = dfic['flatDiscreteWorld'].apply(g.convert_to_str)

max_actions = dfic['blockNum'].max()

### make trajectory graph

In [20]:
importlib.reload(g) ## reimport graph utils
make_plot = True
if make_plot:
    phases = ['pre', 'post']
    for this_target in targets:
        for this_phase in phases:
            g.plot_trajectory_graph(data = dfic, 
                                    target = this_target, 
                                    phase = this_phase, 
                                    save=False, 
                                    out_dir = plot_dir,
                                    extension = 'test',
                                    x_lower_bound = 4,
                                    x_upper_bound = 13,
                                    edge_width_scale_factor = 0.4,
                                    node_size_scale_factor = 0.4)

/Users/will/anaconda3/lib/python3.7/site-packages/scipy/ndimage/measurements.py:1359: RuntimeWarning:

invalid value encountered in double_scalars



### analyze sparsity over world states

In [21]:
importlib.reload(g)
H = dict()
P = dict()
phases = ['pre', 'post']
for target in targets:
    H[target] = dict()
    P[target] = dict()
    for phase in phases:
        print('Calculating sparsity metric for {} {}'.format(target, phase))
        h,p = g.get_sparsity_over_states(data=dfic, target=target, phase=phase, metric='mean')
        H[target][phase] = h
        P[target][phase] = p
        clear_output(wait=True)
print('Done!')

Done!


In [22]:
H2 = pd.DataFrame(H).transpose().reset_index()
H2['diff'] = H2['post']-H2['pre']
importlib.reload(g)

print('**Mean difference in states visited in each phase**')
## bootstrapped CI on difference in mean states visited
U,lb,ub,p1,p2 = g.bootstrapCI(H2['diff'].values, verbose=True)
## paired t-test on difference in mean states visited
g.prettyTtest(H2['diff'].values)

print('-------')
print('**Mean states visited in each phase**')
## bootstrapped CIs on mean states visited in each phase
for phase in phases:
    print('{}'.format(phase))
    U,lb,ub,p1,p2 = g.bootstrapCI(H2[phase].values, verbose=True, compareNull=False)

**Mean difference in states visited in each phase**
Original mean = 0.39047. Bootstrapped mean = 0.38615.
95% CI = [0.22667, 0.55266].
p<0=0.0 | p>0=2.0.
t(7) = 4.23909 | p = 0.00384
-------
**Mean states visited in each phase**
pre
Original mean = 2.02391. Bootstrapped mean = 2.02454.
95% CI = [1.8586, 2.18661].
post
Original mean = 2.41438. Bootstrapped mean = 2.41069.
95% CI = [2.15383, 2.64395].


In [23]:
H2

index       pre      post      diff
0  hand_selected_004  1.845041  2.312500  0.467459
1  hand_selected_005  2.373457  2.593373  0.219917
2  hand_selected_006  1.723005  1.814196  0.091192
3  hand_selected_008  1.926714  2.672176  0.745462
4  hand_selected_009  2.151584  2.947075  0.795491
5  hand_selected_011  2.182768  2.552163  0.369395
6  hand_selected_012  2.252847  2.479029  0.226181
7  hand_selected_016  1.735883  1.944544  0.208660

### Analyze set relationships between pre states and post states

In [24]:
NS = dict() # num states dict
for target in targets:
    NS[target] = dict()
    PRE = set(P[target]['pre'].keys())
    POST = set(P[target]['post'].keys())
    xsect = PRE.intersection(POST)
    u = PRE.union(POST)
    overlap = list(xsect)
    post_prop = np.sum([P[target]['post'][o] for o in overlap])
    pre_prop = np.sum([P[target]['pre'][o] for o in overlap])    
    NS[target]['pre'] = len(PRE)
    NS[target]['post'] = len(POST)
    NS[target]['xsect'] = len(xsect)
    NS[target]['union'] = len(u)
    NS[target]['pre_overlap'] = pre_prop
    NS[target]['post_overlap'] = post_prop   
    NS[target]['diff'] = len(POST) - len(PRE)
    print('{} | Pre: {} | Post: {} | Intrsct: {} | Union: {} | PreOverlap: {} | PostOverlap: {}'.
          format(target, len(PRE),len(POST),len(xsect), len(u), pre_prop.round(4),post_prop.round(4)))

## create num states dataframe 
ND = pd.DataFrame.from_dict(NS, orient='index').reset_index()    

hand_selected_004 | Pre: 484 | Post: 448 | Intrsct: 134 | Union: 798 | PreOverlap: 0.5756 | PostOverlap: 0.6641
hand_selected_005 | Pre: 324 | Post: 332 | Intrsct: 92 | Union: 564 | PreOverlap: 0.6697 | PostOverlap: 0.7027
hand_selected_006 | Pre: 426 | Post: 479 | Intrsct: 110 | Union: 795 | PreOverlap: 0.545 | PostOverlap: 0.5443
hand_selected_008 | Pre: 423 | Post: 363 | Intrsct: 96 | Union: 690 | PreOverlap: 0.5681 | PostOverlap: 0.7021
hand_selected_009 | Pre: 442 | Post: 359 | Intrsct: 114 | Union: 687 | PreOverlap: 0.6225 | PostOverlap: 0.7401
hand_selected_011 | Pre: 383 | Post: 393 | Intrsct: 102 | Union: 674 | PreOverlap: 0.6292 | PostOverlap: 0.662
hand_selected_012 | Pre: 439 | Post: 453 | Intrsct: 152 | Union: 740 | PreOverlap: 0.6795 | PostOverlap: 0.7026
hand_selected_016 | Pre: 549 | Post: 559 | Intrsct: 181 | Union: 927 | PreOverlap: 0.5782 | PostOverlap: 0.6109


In [25]:
ND

index  pre  post  xsect  union  pre_overlap  post_overlap  diff
0  hand_selected_004  484   448    134    798     0.575588      0.664093   -36
1  hand_selected_005  324   332     92    564     0.669701      0.702671     8
2  hand_selected_006  426   479    110    795     0.544959      0.544304    53
3  hand_selected_008  423   363     96    690     0.568098      0.702062   -60
4  hand_selected_009  442   359    114    687     0.622503      0.740076   -83
5  hand_selected_011  383   393    102    674     0.629187      0.662014    10
6  hand_selected_012  439   453    152    740     0.679474      0.702582    14
7  hand_selected_016  549   559    181    927     0.578174      0.610856    10

In [26]:
## difference in total num states visited between pre and post
importlib.reload(g)
g.statsPrint(ND['diff'].values)

t(7) = -0.66004 | p = 0.53034
Original mean = -10.5. Bootstrapped mean = -9.88538.
95% CI = [-38.3875, 18.4].
p<0=1.444 | p>0=0.554.


### calculate sparsity over state-state transitions

In [ ]:
importlib.reload(g)
H = dict()
P = dict()
phases = ['pre', 'post']
for target in targets:
    H[target] = dict()
    P[target] = dict()
    for phase in phases:
        print('Calculating sparsity for {} {}'.format(target, phase))
        h, E = g.get_sparsity_over_edges(data=dfic, target=target, phase=phase, metric='mean')
        H[target][phase] = h
        P[target][phase] = E
        clear_output(wait=True)
print('Done!')   

Calculating sparsity for hand_selected_016 pre


In [ ]:
H2 = pd.DataFrame(H).transpose().reset_index()
H2['diff'] = H2['post']-H2['pre']
importlib.reload(g)

print('**Mean difference in state-state transitions taken in each phase**')
## bootstrapped CI on difference in mean states visited
U,lb,ub,p1,p2 = g.bootstrapCI(H2['diff'].values, verbose=True)
## paired t-test on difference in mean states visited
g.prettyTtest(H2['diff'].values)

print('-------')
print('**Mean state-state transitions taken in each phase**')
## bootstrapped CIs on mean states visited in each phase
for phase in phases:
    print('{}'.format(phase))
    U,lb,ub,p1,p2 = g.bootstrapCI(H2[phase].values, verbose=True, compareNull=False)

AttributeError: module 'pandas' has no attribute 'dataframe'